# Behavioral Analysis Tools
To promote easy analysis of behavioral data, here we outline and give examples of segmentation and annotation tools available in the behavioral_analysis folder of the Github repository found here: https://github.com/julianmwagner/sceptovideo.

We first import the required packages.

In [2]:
import numpy as np
import pandas as pd

#needed for image analysis
import skimage.io
import skimage.filters
import skimage.morphology

#plotting packages
import bokeh.io
import bokeh.layouts

#for loading many image files
import glob
import re

#for progress bars on iterations
import tqdm

from multiprocessing import Pool

# this modlule should be locally installed, and is available at
#https://github.com/justinbois/bootcamp
import bootcamp_utils

#local py files with analysis functions
import segmentation
import traintools
import utilities

#for timing of functions (test speed improvements)
%load_ext line_profiler

bokeh.io.output_notebook()

Loading BokehJS ...

The functions implemented in `segmentation` and `traintools` have a test suite stored in `tests` folder. To run `pytest` on these functions, uncomment the following.

In [28]:
!pytest -v ../tests/test_segmentation_pipeline.py

============================= test session starts ==============================
platform darwin -- Python 3.6.5, pytest-3.5.1, py-1.5.3, pluggy-0.6.0 -- /Users/julianwagner/anaconda3/bin/python
cachedir: ../.pytest_cache
rootdir: /Users/julianwagner/git/sceptovideo, inifile:
plugins: remotedata-0.2.1, openfiles-0.3.0, doctestplus-0.1.3, arraydiff-0.2, hypothesis-3.57.0
collected 29 items                                                             

../tests/test_segmentation_pipeline.py::test_im_shape PASSED             [  3%]
../tests/test_segmentation_pipeline.py::test_im_data_type_list PASSED    [  6%]
../tests/test_segmentation_pipeline.py::test_im_data_type_string PASSED  [ 10%]
../tests/test_segmentation_pipeline.py::test_im_shape_segment PASSED     [ 13%]
../tests/test_segmentation_pipeline.py::test_im_data_type_list_segment PASSED [ 17%]
../tests/test_segmentation_pipeline.py::test_im_data_type_string_segment PASSED [ 20%]
../tests/test_segmentation_pipeline.py::test_provided_

When working with time series images, it is vitally important to check that they are read in the correct order. We just take a look at the image names in the folder of processing and access whether they will be read properly.

In [4]:
!ls ../toy_data/

ant_scepto-04092018133745-6089.tiff ant_scepto-04092018133745-6105.tiff
ant_scepto-04092018133745-6090.tiff ant_scepto-04092018133745-6106.tiff
ant_scepto-04092018133745-6091.tiff ant_scepto-04092018133745-6107.tiff
ant_scepto-04092018133745-6092.tiff ant_scepto-04092018133745-6108.tiff
ant_scepto-04092018133745-6093.tiff ant_scepto-04092018133745-6109.tiff
ant_scepto-04092018133745-6094.tiff ant_scepto-04092018133745-6110.tiff
ant_scepto-04092018133745-6095.tiff ant_scepto-04092018133746-6111.tiff
ant_scepto-04092018133745-6096.tiff ant_scepto-04092018133746-6112.tiff
ant_scepto-04092018133745-6097.tiff ant_scepto-04092018133746-6113.tiff
ant_scepto-04092018133745-6098.tiff ant_scepto-04092018133746-6114.tiff
ant_scepto-04092018133745-6099.tiff ant_scepto-04092018133746-6115.tiff
ant_scepto-04092018133745-6100.tiff ant_scepto-04092018133746-6116.tiff
ant_scepto-04092018133745-6101.tiff ant_scepto-04092018133746-6117.tiff
ant_scepto-04092018133745-6102.tiff ant_scepto-04092018133746-61

We can already tell that these files will probably not read in correctly due to the string of numbers before the second set of indexing numbers. We can verify this failure by performing a glob command and checking the first two file names.

In [5]:
glob.glob('../toy_data/ant_*.tiff')[0:2]

['../toy_data/ant_scepto-04092018133745-6094.tiff',
 '../toy_data/ant_scepto-04092018133745-6104.tiff']

This file ordering is clearly erroneous. We will need to write a function to re-order the globed list of file names before reading in the images. These images come from a FLIR camera, so we name the function accordingly. We will store this function in a utilities.py file for general use, which the user can reference if desired.

In [6]:
im_fs = utilities.fix_FLIR_file_order(glob.glob('../toy_data/ant_*.tiff'))
im_fs[0:10]

['../toy_data/ant_scepto-04092018133745-6089.tiff',
 '../toy_data/ant_scepto-04092018133745-6090.tiff',
 '../toy_data/ant_scepto-04092018133745-6091.tiff',
 '../toy_data/ant_scepto-04092018133745-6092.tiff',
 '../toy_data/ant_scepto-04092018133745-6093.tiff',
 '../toy_data/ant_scepto-04092018133745-6094.tiff',
 '../toy_data/ant_scepto-04092018133745-6095.tiff',
 '../toy_data/ant_scepto-04092018133745-6096.tiff',
 '../toy_data/ant_scepto-04092018133745-6097.tiff',
 '../toy_data/ant_scepto-04092018133745-6098.tiff']

We can see that this fixed the image ordering. I cannot emphasize enough that you must **take great care that the images are read in the proper order**. Wrongly ordered images will lead to frustration and wrong results down the line. We can now read in the images stored at the ordered file names and store them in a list. We also read in `im_bg` which is a picture of the behavioral arena of concern without any animals in it. This will be used for background subtraction.

In [7]:
ims = [skimage.io.imread(x) for x in im_fs]
im_bg = skimage.io.imread('../toy_data/col_filed.tiff')

We can now take a look at one of the images to see what we are dealing with.

In [8]:
bokeh.io.show(bootcamp_utils.viz.bokeh_imshow(ims[0]))

There are large areas of this image that are not of interest for our analysis. We have a couple of options for how to deal with non-relavent areas of the image. We could set areas outside of the region of interest to a constant value to remove the chance that they are counted as blobs in a segmentation procedure. We could also crop to a smaller rectangular region of the image for consideration. We demonstrate the use of the `segmentation` functions to perform such tasks.

In [9]:
im_roi = segmentation.give_roi_of_image(ims[0],
                                        cent=((200, 238), (461, 232)),
                                        roi_kind=('ellipse', 'ellipse'),
                                        height=(126, 126),
                                        width=(126, 126))

im_crop = segmentation.crop_image_rectangle(ims[0],
                                        cent=(200, 238),
                                        height=126,
                                        width=126)
bokeh.io.show(bokeh.layouts.row(bootcamp_utils.viz.bokeh_imshow(im_roi),
                                bootcamp_utils.viz.bokeh_imshow(im_crop)))

Much of the variation in the background of the images can be eliminated by doing a background subtraction on the image. We use the image of the empty arena as the background for the subtraction. Note that the background subtraction function normalizes the inputs for better results. Once the background has been removed, segmentation is much more straight forward. We feed this image into the `segment` function and use Otsu's method to automatically determine the threshold value. 

In [10]:
im_no_bg = segmentation.bg_subtract(ims[0], im_bg)
im_cropped = segmentation.crop_image_rectangle(im_no_bg,
                                        cent=(200, 238),
                                        height=126,
                                        width=126)
im_bw, _, _ = segmentation.segment(im_cropped, thresh_func=lambda x: skimage.filters.threshold_otsu(x) + 0.15)
bokeh.io.show(bokeh.layouts.row([bootcamp_utils.bokeh_imshow(im_cropped),
                                   bootcamp_utils.bokeh_imshow(im_bw)]))

In [14]:
bokeh.io.show(bootcamp_utils.viz.bokeh_imshow(im_bg_construct))

We could also use a constant value for the threshold in this function. Here we show a background subtracted image with an ROI segmented based on a constant threshold value that was manually chosen.

In [11]:
im_no_bg = segmentation.bg_subtract(ims[0], im_bg)
im_roi = segmentation.give_roi_of_image(im_no_bg,
                                        cent=((200, 238), (461, 232)),
                                        roi_kind=('ellipse', 'ellipse'),
                                        height=(126, 126),
                                        width=(126, 126))
im_bw, _, _ = segmentation.segment(im_roi, thresh_func=0.65)
bokeh.io.show(bokeh.layouts.row([bootcamp_utils.bokeh_imshow(im_roi),
                                   bootcamp_utils.bokeh_imshow(im_bw)]))

Using these tools, as well as functions from skimage, we demonstrate how to construct a pipeline for analysis on a set of images from a behavioral experiment. Analyzing images via a segmentation approach is trivially parallelizable: analysis on a given image does not depend on the previous or subsequent frame. This lends itself to use of the `Pool` class in python. This allows the user to spawn 'workers' (e.g. a worker per CPU core) that then each independently perform the requisite calculations before the data is combined. When running a `pool`, the provided function can only take one argument, so you need to make a function that takes a tuple of arguments that then calls the image processing function if it has multiple arguments.

In [12]:
#the pipeline for image analysis
def process_image(im, im_bg, ind, return_labels=False):
    attributes = []
    #background subtraction and ROI selection
    im_no_bg = segmentation.bg_subtract(im, im_bg)
    im_roi = segmentation.give_roi_of_image(im_no_bg,
                                            cent=((200, 238), (461, 232)),
                                            roi_kind=('ellipse', 'ellipse'),
                                            height=(126, 126),
                                            width=(126, 126))
    im_bw, im_lab, n_labs = segmentation.segment(im_roi, thresh_func=0.6)
    #removes objects smaller than 20 square pixels 
    im_bw_no_small = skimage.morphology.remove_small_objects(im_lab, min_size=20)
    #calculate the regionprops for the thresholded image. This gets properties of the contiguous blobs in the image
    blobs = skimage.measure.regionprops(im_bw_no_small, intensity_image=im)
    
    #parse and return the scalar features of each blob detected in the images
    for blob in blobs:
        atts, labs = segmentation.region_props_to_tuple(blob)
        attributes.append((ind, *atts))
    if return_labels:
        return attributes, labs
    return attributes

#a dummy function that takes a tuple for an argument and calls the process image pipeline
def fn(args):
    return process_image(*args)

#run the function on multiple threads for faster results and return a tuple of tuples with blob properties for each
#blob in each frame of the serries of images.
def multi_proc_image(ims, im_bg, proc_num=4):
    with Pool(processes=proc_num) as p:
        attributes = list(tqdm.tqdm_notebook(
                          p.imap(fn, [(im, im_b, i) for im, im_b, i in zip(ims, [im_bg]*len(ims), range(len(ims)))]),
                          total=len(ims)))
    
    attribs = []
    for line in attributes:
        for lin in line:
            attribs.append(lin)
    return attribs

With these functions defined, we can now run the pipeline on all the images.

In [13]:
attributes = multi_proc_image(ims, im_bg, proc_num=4)
_, labs = process_image(ims[0], im_bg, 0, return_labels=True)

We can now take a look at the data that we generated.

In [14]:
pd.DataFrame(attributes, columns=('frame_num', *labs)).head(5)

frame_num  area  bbox_min_row  bbox_min_col  bbox_max_row  bbox_max_col  \
0          0   374           128           135           178           158   
1          0   304           209           400           241           421   
2          0  1225           211           161           289           215   
3          0  1214           247           377           291           447   
4          1   359           134           134           176           152   

   bbox_area  centroid_row  centroid_col  convex_area  \
0     307200    155.467914    143.639037          588   
1     307200    225.325658    411.207237          379   
2     307200    247.025306    185.662857         2933   
3     307200    268.958814    407.927512         1998   
4     307200    154.835655    142.668524          517   

              ...               mean_intensity  min_intensity  \
0             ...                    73.727273             31   
1             ...                    64.009868             26   
2             ...                    73.069388             17   
3             ...                    62.081549             18   
4             ...                    70.139276             30   

   minor_axis_length  orientation   perimeter  solidity  \
0          12.413753     1.306656  126.704581  0.636054   
1          11.737283    -1.043963   92.426407  0.802111   
2          34.314128    -1.513199  400.563492  0.417661   
3          26.222183    -0.312971  322.663997  0.607608   
4          12.131516     1.378727  108.840620  0.694391   

   weighted_centroid_row  weighted_centroid_col  weighted_local_centoid_row  \
0             153.729999             144.322079                   25.729999   
1             224.124827             410.458862                   15.124827   
2             249.158496             186.152229                   38.158496   
3             269.706914             410.445832                   22.706914   
4             153.734829             142.910564                   19.734829   

   weighted_local_centroid_col  
0                     9.322079  
1                    10.458862  
2                    25.152229  
3                    33.445832  
4                     8.910564  

[5 rows x 30 columns]

For later analysis, we will extract the subimage for each of these blobs and store them in a list. The reasons for this will become clear later.

In [15]:
blob_rois = [segmentation.bg_subtract(ims[x[0]], im_bg)[x[2]:x[4], x[3]:x[5]] for x in tqdm.tqdm_notebook(attributes)]

# In-notebook labeling of images for network training

In order to work with deep learning tools for analysis, a user must provide some sort of annotated data set. Here are a couple of tools for quick labeling of specified images directly in the jupyter notebook.

### Adding point labels to a plot
The first tool is used to generate point coordinates on an image and store the labels in a `bokeh` `ColumnDataSource` from which a `DataFrame` of the points can easily be accessed. The user simply provides the images that they wish to view and the function generates an interactive plot for point labeling. Note that the function returns the `ColumnDataSource` object so that the user can work with it after finishing setting labels. Note that to access the point tool used to generate data points, you must click the icon on the side of the plot that looks like this:  <img src="point_tool.png" alt="drawing" width="30px"/>. Use either the slider of the buttons to move from frame to frame.

In [16]:
point_labels = traintools.point_label(ims)

### Classification of blobs

The other tool is designed for classification tasks. It allows the user to supply a tuple of label types for a set of images and iterate through the images and label them. The GUI is quite similar to the previous one.

In [18]:
blob_labels = traintools.button_label(blob_rois, ('beetle', 'ant', 'other'))